# Homework 5: Deutch Algorithm and Grover's Search
$$
\newcommand{\ket}[1]{\left| #1 \right\rangle}
\newcommand{\bra}[1]{\left\langle #1 \right|}
\newcommand{\braket}[2]{\left\langle #1 | #2 \right\rangle}
$$

In [ ]:
# Import packages
import math

from qiskit import QuantumCircuit, transpile, QuantumRegister, ClassicalRegister
from qiskit.circuit.library import MCMTGate, XGate
from qiskit.quantum_info import Statevector
from qiskit.visualization import plot_distribution
from qiskit_ibm_runtime import SamplerV2 as Sampler
from qiskit_aer import Aer

backend = Aer.get_backend('qasm_simulator')

For your convenience, we created a simulation function, so you can simply input quantum circuit (qc), shots, and the backend you use, it will return the simulation counts.

In [ ]:
# simulation function
# qc -- Quantum Circuit
# backend -- Quantum Simulator or IBM machine
# returns --> counts
def simulate(qc, shots, backend):
    t_qc = transpile(qc, backend)
    sampler = Sampler(backend)
    sampler.options.default_shots = shots
    result = sampler.run([t_qc]).result()
    counts = result[0].data['c_reg'].get_counts()
    return counts

## Part I -- Deutch's Algorithm

In Deutch's Algorithm, we are trying to distinguish the unbalanced and balanced situation:
$$
f(0)=f(1) \ or \ f(0) \ne f(1)
$$
So let's take the example for the unbalanced case $f(0) = f(1) = 0$.

#### Step 1: Prepare the state.
Our initialization is $\ket{01}$, so we need to put a Pauli-X gate at the begining of the second qubit.

After state preparation we will get
$$
\ket{x} = \frac{\ket{0} + \ket{1}}{\sqrt{2}}, \ket{y} = \frac{\ket{0} - \ket{1}}{\sqrt{2}}
$$

In [ ]:
qr = QuantumRegister(2, 'q_reg')
cr = ClassicalRegister(1, 'c_reg')
state_prep = QuantumCircuit(qr, cr, name='state prep')

# State preparation
state_prep.x(qr[1])
state_prep.barrier()
state_prep.h(qr)
state_prep.barrier()
state_prep.draw(output='mpl')

#### Step 2: Create the oracle for $U_{f0}$.

Let's create an oracle for the unbalanced situation $U_{f0}$. Note that in this case, $f(0) = f(1) = 0$

In class, we discussed the functionality of Deutsch's Oracle as $U_f\ket{x, y} = \ket{x, y \oplus f(x)}$. And use the notation of $f_0$ in class, we will have the truth table:

|x|y|$f_0$| $y\oplus f_0$ |
|:--:|:--:|:--:|:-------------:|
|0|0|0|       0       |
|0|1|0|1|
|1|0|0|0|
|1|1|0|1|



Thinking of converting the input and output to transfer matrix, you will get
$$
U_{f0} =
\begin{bmatrix}
1 & 0 & 0 & 0 \\
0 & 1 & 0 & 0 \\
0 & 0 & 1 & 0 \\
0 & 0 & 0 & 1
\end{bmatrix}.
$$

Obviously it's Identity matrix, the evolved state will stay the same.

In [ ]:
# Deutch's Oracle for U_f0 -> f(0) = f(1) = 0
oracle = QuantumCircuit(qr, cr, name='oracle')
oracle.id(qr)
oracle.barrier()
oracle.draw(output='mpl')

#### Step 3: Put an additional Hadamard gate on the measurement qubit.
After the hadamard gate, you will have
$$
\pm \ket{0} \frac{\ket{0}-\ket{1}}{\sqrt{2}}
$$

In [ ]:
# Hadamard
state_ret = QuantumCircuit(qr, cr, name='state retrieve')
state_ret.h(qr[0])
state_ret.barrier()
state_ret.draw(output='mpl')

#### Step 4: Connect all components to a complete circuit and test.

We use *qc.compose()* to connect separate circuits.

In [ ]:
# Circuit connection
qc = QuantumCircuit(qr, cr, name='qc')
qc.compose(state_prep, inplace=True)
qc.compose(oracle, inplace=True)
qc.compose(state_ret, inplace=True)

qc.measure(qr[0], cr)
qc.draw(output='mpl')

In [ ]:
dist = simulate(qc, shots=1024, backend=backend)
plot_distribution(dist)

You will measure the result as $\ket{0}$, which indicates unbalanced.

### Question 1: Create the oracle for the case for $U_{f01}: f(0) = 0, f(1) = 1$ discussed in class, and verify it by visualization (histogram or statevector on bloch sphere).

In [ ]:
# Insert the answer to Question 1 HERE.

## Part II -- Grover's Search Algorithm

- In this part, we focus on an example of a 2-bit searching algorithm.
- The phase flipping equation follows
$$
f(x)=\left\{
\begin{aligned}
 & \ket{x}, &x = x_0 \\
  -&\ket{x}, &x \ne x_0
\end{aligned}
\right.,
$$
where in the superposition state, if there is the target state, we flip the phase on that state. We will guide through the evolving in the following sections.

#### Step 1: Prepare the superposition state.
In this stage, we initialize the database to the superposition state contains all the possible outcome.

And we prepare an additional ancilla qubit and initialize it to $\frac{\ket{0}-\ket{1}}{\sqrt{2}}$.

In [ ]:
data = QuantumRegister(2, 'data')
ancilla = QuantumRegister(1, 'ancilla')
cr = ClassicalRegister(2, 'c_reg')
state_prep = QuantumCircuit(data, ancilla, cr, name='state prep')

state_prep.x(ancilla)
state_prep.barrier()
state_prep.h(data)
state_prep.h(ancilla)
state_prep.barrier()
state_prep.draw(output='mpl')

#### Step 2: Create the oracle for finding bitstring $10$
In order to mark the position of **10**, we will need to set the coefficient in second entry to -1. The evolving is shown as follows
$$
U_f \frac{1}{2} \begin{bmatrix} 1 \\ 1 \\ 1 \\ 1 \end{bmatrix} = \frac{1}{2} \begin{bmatrix} 1 \\ 1 \\ -1 \\ 1 \end{bmatrix}.
$$
To implement this function, we will need the ancilla qubit to perform a **phase kickback**, which the phase in the target qubit will affect the control qubit.

We can formalize the state with ancilla as
$$
\ket{\psi} = (-1)^{f(x)}\ket{x} [\frac{\ket{0} - \ket{1}}{\sqrt{2}}]
$$
And combining how we create $\ket{x, y} \rightarrow \ket{x, y \oplus f(x)}$, we will get the transfer matrix $U_f$ as
$$
\begin{bmatrix}
1 & 0 & 0 & 0 & 0 & 0 & 0 & 0 \\
0 & 1 & 0 & 0 & 0 & 0 & 0 & 0 \\
0 & 0 & 1 & 0 & 0 & 0 & 0 & 0 \\
0 & 0 & 0 & 1 & 0 & 0 & 0 & 0 \\
0 & 0 & 0 & 0 & 0 & 1 & 0 & 0 \\
0 & 0 & 0 & 0 & 1 & 0 & 0 & 0 \\
0 & 0 & 0 & 0 & 0 & 0 & 1 & 0 \\
0 & 0 & 0 & 0 & 0 & 0 & 0 & 1 \\
\end{bmatrix}
$$
We will know that this matrix can be synthesized to a **toffoli-gate** with the second qubit inverted, and note that the data in qiskit is encoded in a **little endian** manner (**MSB to 1st qubit, LSB to last qubit**), so instead of inverting second qubit, we invert first qubit.


In [ ]:
# Grover's Oracle for 10
oracle = QuantumCircuit(data, ancilla, cr, name='Uf')
oracle.x(data[0])
oracle.compose(MCMTGate(XGate(), oracle.num_qubits - 1, 1), inplace=True) # Toffoli-gate
oracle.x(data[0])
oracle.barrier()
oracle.draw(output='mpl')

#### Step 3: Create the circuit for "Inversion about Mean (IaM)" function.

Note that the transfer matrix of $-I_n + 2A_n$ is

$$
\begin{bmatrix}
(-1 + 2/2^n) & 2/2^n & \cdots & 2/2^n \\
2/2^n & (-1 + 2/2^n) & \cdots & 2/2^n \\
\vdots & \vdots & \ddots & \vdots \\
2/2^n & 2/2^n & \cdots & (-1+2/2^n)
\end{bmatrix}
$$

It will be slightly complicated for you to synthesize the circuit, but here I will give you the factory format for this circuit.
$$
(HX)^{\otimes n} H_n \cdot CCX \cdot H_n (XH)^{\otimes n}
$$

In [ ]:
# Inversion about mean in two-qubit situation
iam = QuantumCircuit(data, ancilla, cr, name='iam')
iam.h(data)
iam.x(data)
iam.barrier()

iam.h(data[1])
iam.cx(data[0], data[1])
iam.h(data[1])
iam.barrier()

iam.x(data)
iam.h(data)
iam.barrier()

iam.draw(output='mpl')

#### Step 4: Calculate iteration and connect components.
Note that you need to iterate the **$U_f$** and **IaM** to improve the search precision. Here we calculate the optimal number of iteration [1] as
$$
I_{opt} =
\left\lfloor
\frac{\pi}{4 \, \arcsin\!\left( \sqrt{\dfrac{M}{2^n}} \right)}
\right\rfloor,
$$
where $M$ represents the number of target state, $n$ is the number of the qubit.

[1] Boyer, M., Brassard, G., Høyer, P., & Tapp, A. (1998). Tight bounds on quantum searching. Fortschritte der Physik: Progress of Physics, 46(4‐5), 493-505.

In [ ]:
# calculate interation
optimal_num_iterations = math.floor(
    math.pi/ (4 * math.asin(math.sqrt(1 / 2 ** (data.size)))) # Since we are just marking 1 target state, M = 1
)
print("Iteration:",optimal_num_iterations)

# Circuit concat
qc = QuantumCircuit(data, ancilla, cr, name='qc')
qc.compose(state_prep, inplace=True)
for i in range(optimal_num_iterations):
    qc.compose(oracle, inplace=True)
    qc.compose(iam, inplace=True)
print(Statevector.from_instruction(qc))
qc.measure(data, cr)
qc.draw(output='mpl')

In [ ]:
dist = simulate(qc, shots=10000, backend=backend)
print(dist)

In [ ]:
plot_distribution(dist)

### Question 2: Create a circuit searching for bitstring 001.

For your convenience, I will provide the circuit for state preparation and inversion about mean for 3-bit search, your task will be creating the **oracle** for search **bitstring 001**.

#### Step 1: State preparation

In [ ]:
data = QuantumRegister(3, 'data')
ancilla = QuantumRegister(1, 'ancilla')
cr = ClassicalRegister(3, 'c_reg')
state_prep = QuantumCircuit(data, ancilla, cr, name='state prep')

state_prep.x(ancilla)
state_prep.barrier()
state_prep.h(data)
state_prep.h(ancilla)
state_prep.barrier()
state_prep.draw(output='mpl')

#### Step 2: Create a grover's oracle for 001 (Your task)

In [ ]:
# Grover's Oracle for 001
oracle = QuantumCircuit(data, ancilla, cr, name='Uf')

# Insert your answer here

oracle.barrier()
oracle.draw(output='mpl')

#### Step 3: Create IaM in 3-qubit scenario

In [ ]:
# Inversion about mean in three-qubit scenario
iam = QuantumCircuit(data, ancilla, cr, name='iam')
iam.h(data)
iam.x(data)
iam.barrier()

iam.h(data[2])
iam.compose(MCMTGate(XGate(), data.size - 1, 1), inplace=True)
iam.h(data[2])
iam.barrier()

iam.x(data)
iam.h(data)
iam.barrier()

iam.draw(output='mpl')

#### Step 4: Calculate iteration and connect circuit.

In [ ]:
# calculate interation
optimal_num_iterations = math.floor(
    math.pi/ (4 * math.asin(math.sqrt(1 / 2 ** (data.size)))) # Since we are just marking 1 target state, M = 1
)
print("Iteration:",optimal_num_iterations)

# Circuit concat
qc = QuantumCircuit(data, ancilla, cr, name='qc')
qc.compose(state_prep, inplace=True)
for i in range(optimal_num_iterations):
    qc.compose(oracle, inplace=True)
    qc.compose(iam, inplace=True)
print(Statevector.from_instruction(qc))
qc.measure(data, cr)
qc.draw(output='mpl')

In [ ]:
dist = simulate(qc, shots=10000, backend=backend)
print(dist)

In [ ]:
plot_distribution(dist)

### Question 3: From the histogram distribution above, if your circuit is correct, you will notice that there still exists the probabilities of getting other outputs. Can you explain why this is happening?

Insert the answer to Question 3 HERE.

### Bonus question: Think of a quantum algorithm from whatever you have learned in class that can be applied to solve a real-world problem. Describe the practical scenario where your algorithm will be used. You don’t need to provide the specific circuit code, just briefly explain how the algorithm’s functionality addresses the chosen problem.

Insert the answer to Bonus question HERE.

### Export this Notebook to HTML, and send it to yayum@smu.edu and mitch@smu.edu.